In [ ]:
import os
import glob
import torchvision.transforms as transforms
import torch
from PIL import Image
from torch.utils.data import Dataset, DataLoader

# MNIST 이미지 경로
secret_path = '../../mnist/'
clean_path ='../secret/clean.png'

# 이미지 변환 설정: 크기 조정 및 텐서로 변환
transform = transforms.Compose([
    transforms.Resize((256, 256)),  # 크기를 28x28로 조정
    transforms.Grayscale(num_output_channels=3),  # 1채널을 3채널로 변환
    transforms.ToTensor()
])

# MNIST 데이터셋 경로
secret_test_mnists = sorted(glob.glob(secret_path + '/test/' + '*/*.png'))
secret_train_mnists = sorted(glob.glob(secret_path + '/train/' + '*/*.png'))
secret_valid_mnists = glob.glob(secret_path + '/valid/' + '*/*.png')

class CustomDataset(Dataset):
    def __init__(self, file_list, transform):
        self.file_list = file_list
        self.transform = transform

    def __len__(self):
        return len(self.file_list)

    def __getitem__(self, idx):
        img_path = self.file_list[idx]
        image = Image.open(img_path).convert('L')  # 흑백 이미지로 변환
        image = self.transform(image)
        return image

# 데이터셋 및 데이터 로더 생성
secret_train_dataset = CustomDataset(secret_train_mnists, transform)
secret_test_dataset = CustomDataset(secret_test_mnists, transform)
secret_valid_dataset = CustomDataset(secret_valid_mnists, transform)

secret_Trainloader = DataLoader(secret_train_dataset, batch_size=8, shuffle=True, num_workers=1)
secret_Testloader = DataLoader(secret_test_dataset, batch_size=8, shuffle=False, num_workers=1)
secret_Validloader = DataLoader(secret_valid_dataset, batch_size=8, shuffle=False, num_workers=1)

# 데이터셋에서 첫 번째 배치 가져오기
secret_train = next(iter(secret_Trainloader))

print("| Train Size : ", len(secret_train_mnists), "| Test Size : ", len(secret_test_mnists), "| Valid Size : ", len(secret_valid_mnists)," |")
print("Secret Img Shape : ", secret_train.size())


In [ ]:
import matplotlib.pyplot as plt 

col, row = 8, 2
fig = plt.figure(figsize=(12, 6))
for i in range(1, col * row + 1):
    img = secret_train_dataset[i-1]  # 데이터셋에서 이미지 가져오기
    img = img.permute(1, 2, 0).numpy()  # 텐서를 NumPy 배열로 변환

    fig.add_subplot(row, col, i)
    plt.imshow(img, cmap='gray')
    plt.title(secret_train_mnists[i-1].split('/')[-1].split('.')[0])
    plt.axis('off')

print(img.shape)
plt.show()



In [ ]:
import os
from matplotlib.image import imread
import matplotlib.pyplot as plt

train_path = "./outputs/trainPics/gold__1203-10_29/"
valid_path = "./outputs/validationPics/gold__1203-10_29/"

idx = 0
path_index = [train_path, valid_path]
target_path = path_index[idx]

image_names = []
for filename in os.listdir(target_path):
    if filename.endswith(".png"):
        image_names.append(filename)
        
image_names = sorted([filename for filename in os.listdir(target_path) if filename.endswith(".png")])
# print(image_names)

epochs = []
batches = []
for name in image_names:
    epoch, batch = name.split("_")[1:3]
    epochs.append(epoch)
    batches.append(batch)

unique_epochs = sorted(list(set(epochs)))

if target_path == train_path:
    unique_batches = ["0000", "0500", "1100", "1700"]
elif target_path == valid_path:
    unique_batches = ["0000", "0050", "150", "200"]


fig = plt.figure(figsize=(12, 15))
fig.suptitle(f"Train Result", y=1.0)
for epoch_idx, epoch in enumerate(unique_epochs):
    for batch_idx, batch in enumerate(unique_batches):
        image_name = f"ResultPics_{epoch}_batch{batch}.png"
        image_path = os.path.join(target_path, image_name)

        if os.path.exists(image_path):
            image = imread(image_path)
            ax = fig.add_subplot(len(unique_epochs), len(unique_batches), epoch_idx * len(unique_batches) + batch_idx + 1)
            ax.imshow(image) #[774:1548])
            ax.axis('off')
            ax.set_title(f"{epoch} : batch{batch}")

plt.tight_layout()
plt.show()



In [20]:

import os
import torch
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.image import imread
from models.HidingRes import HidingRes
from skimage.transform import resize
from skimage.metrics import mean_squared_error as MSE
from skimage.metrics import structural_similarity as SSIM
from skimage.metrics import peak_signal_noise_ratio as PSNR
from sklearn.metrics import f1_score as F1

hostname = "gold"
runDate = 1204
runTime = "19_24_51"
dirName = f"{hostname}__{runDate}-{runTime}"       #"gold__1203-10_29/"

train_path = "./outputs/trainPics/" + dirName
valid_path = "./outputs/validationPics/" + dirName
Rnet_path = './outputs/checkPoints/gold__1203-10_29/netR_epoch_21,sumloss=24.817436,Rloss=22.630165.pth'

idx = 1
path_index = [train_path, valid_path]
target_path = path_index[idx]

epochs = []
batches = []
image_names = []
for filename in os.listdir(target_path):
    if filename.endswith(".png"):
        image_names.append(filename)
for name in image_names:
    epoch, batch = name.split("_")[1:3]
    epochs.append(epoch)
    batches.append(batch)
image_names = sorted([filename for filename in os.listdir(target_path) if filename.endswith(".png")])
unique_epochs = sorted(list(set(epochs)))
unique_batches = ["0000", "0500", "1100", "1700"] if target_path == train_path else ["0000", "0050", "0150", "0200"]

Rnet = HidingRes(in_c=3, out_c=3).cuda() 
Rnet.load_state_dict(torch.load(Rnet_path))
Rnet = torch.nn.DataParallel(Rnet)
Rnet.eval()


def crop(image, types):
    h, w, _ = image.shape

    if types == 'random':
        crop_size = np.random.randint(64, min(h, w))
        start_x = np.random.randint(0, w - crop_size)
        start_y = np.random.randint(0, h - crop_size)
        return image[start_y:start_y+crop_size, start_x:start_x+crop_size]

    elif types == 'center':
        center_x, center_y = w // 2, h // 2
        crop_size = min(h, w) // 2
        return image[center_y-crop_size//2:center_y+crop_size//2, center_x-crop_size//2:center_x+crop_size//2]

    elif types == 'corner':
        corner = np.random.choice(['top_left', 'top_right', 'bottom_left', 'bottom_right'])
        crop_size = min(h, w) // 2
        if corner == 'top_left':
            return image[:crop_size, :crop_size]
        elif corner == 'top_right':
            return image[:crop_size, -crop_size:]
        elif corner == 'bottom_left':
            return image[-crop_size:, :crop_size]
        else:  # bottom_right
            return image[-crop_size:, -crop_size:]

    elif types == 'variable':
        crop_size = np.random.randint(64, min(h, w))
        start_x = np.random.randint(0, w - crop_size)
        start_y = np.random.randint(0, h - crop_size)
        return image[start_y:start_y+crop_size, start_x:start_x+crop_size]

    else:
        raise ValueError("Unknown crop type specified")
    
    
def netR(img, cropped=False): 
    if cropped:
        img = crop(img, cropped)
    img_tentsor = torch.from_numpy(img).unsqueeze(0).permute(0, 3, 1, 2).cuda()
    rev_secret = Rnet(img_tentsor).squeeze(0).permute(1, 2, 0).cpu().detach().numpy()
    
    return resize(rev_secret, (256, 256))
    
def getImage(image, row_index, col_index=0):
    size = 256
    rstart = size * row_index + row_index +1
    rend = size * (row_index + 1) + row_index + 1
    
    cstart = size * col_index + col_index +1
    cend = size * (col_index + 1) + col_index + 1
    return image[rstart:rend, cstart:cend]

def ImageLoad(image_path, col_index):
    image = imread(image_path)

    secret = getImage(image, 0, col_index)
    cover_img = getImage(image, 1, col_index)
    clean_img = getImage(image, 2, col_index)
    diff_img = getImage(image, 3, col_index)
    container_img = getImage(image, 4, col_index)
    rev_secret = getImage(image, 5, col_index)
    
    cover_img = resize(cover_img, (256, 256))
    container_img = resize(container_img, (256, 256))
    secret = resize(secret, (256, 256))
    rev_secret = resize(rev_secret, (256, 256))
    
    return cover_img, container_img, clean_img, diff_img, secret, rev_secret

def convertBinary(img, threshhold=0.5):
    img[img > threshhold] = 1
    img[img <= threshhold] = 0
    return img
    
def calculate_metrics(cover_img, container_img, secret, rev_secret, rev_container_secret):
    # 윈도우 크기 설정 (SSIM, PSNR)
    min_side = min(cover_img.shape[0], container_img.shape[1])
    win_size = min_side if min_side % 2 == 1 else min_side - 1
    
    secret = secret * 255
    rev_secret = rev_secret * 255
    rev_container_secret = rev_container_secret * 255
    
    print(np.mean(secret))
    print(np.mean(rev_secret))
    print(np.mean(rev_container_secret))
    
    # SSIM, PSNR 계산
    psnr_img = PSNR(cover_img, container_img)
    ssim_img = SSIM(cover_img, container_img, win_size=win_size, multichannel=True, channel_axis=2, data_range=1)
    psnr_sec = PSNR(secret, rev_secret)
    ssim_sec = SSIM(secret, rev_secret, win_size=win_size, multichannel=True, channel_axis=2, data_range=1)
    psnr_rnet = PSNR(secret, rev_container_secret)
    ssim_rnet = SSIM(secret, rev_container_secret, win_size=win_size, multichannel=True, channel_axis=2, data_range=1)
    
    
    # secret data가 binary인 경우
    if np.max(secret) == 1:
        secret = secret.astype('bool')
        rev_secret = rev_secret.astype('bool')
        rev_container_secret = rev_container_secret.astype('bool')
        f1_rnet = F1(secret, rev_secret, average='micro')
    else :
        f1_rnet = "N/A"
        
    return psnr_img, ssim_img, psnr_sec, ssim_sec, psnr_rnet, ssim_rnet, f1_rnet

def process_data(image_path, col_index, netR, crop=False):
    cover_img, container_img, clean_img, _, secret, rev_secret = ImageLoad(image_path, col_index)
    rev_container_secret = netR(container_img, crop)
    img_metrics = calculate_metrics(cover_img, container_img, secret, rev_secret, rev_container_secret)
    return cover_img, container_img, clean_img, secret, rev_secret, rev_container_secret, img_metrics


def visualize_image(fig, epoch_idx, batch_idx, unique_batches, concat_image, image_metrics):
    ax = fig.add_subplot(len(unique_epochs), len(unique_batches), epoch_idx * len(unique_batches) + batch_idx + 1)
    ax.imshow(concat_image)
    ax.axis('off')
    ax.set_title(f"{epoch} : batch{batch}")

    # 텍스트 추가
    hPos = int(concat_image.shape[0]) + 35
    midPos = int(concat_image.shape[1] / 2)
    for i, metric in enumerate(image_metrics):
        if i % 2 == 0:
            ax.text(15, hPos + (30*i), f"{metric[0]}: {metric[1]:.4f}", fontsize=10, color='white', bbox=dict(facecolor='black', alpha=0.75))
            ax.text(midPos+30, hPos + (30*i) , f"{image_metrics[i+1][0]}: {image_metrics[i+1][1]:.4f}", fontsize=10, color='white', bbox=dict(facecolor='black', alpha=0.75))

metrics = {
    "ipsnr": [], "issim": [],
    # "spsnr": [], "sssim": [],
    "rpsnr": [], "rssim": [], "rf1":[]
}
epoch_metrics = {
    "ipsnr": [], "issim": [],
    # "spsnr": [], "sssim": [],
    "rpsnr": [], "rssim": [], "rf1":[]
}
total_metrics = {
    "ipsnr": [], "issim": [],
    # "spsnr": [], "sssim": [],
    "rpsnr": [], "rssim": [], "rf1":[]
}


# secret 값은 0~1 사이임


for idx in range(0, 20, 5):
    unique_batches.append(f"{idx:04d}")    

col_index = 0 # 0~3
fig = plt.figure(figsize=(4*len(unique_batches), 5 * len(unique_epochs)))
fig.suptitle(f"{target_path.split('/')[2]}", y=1.0)
for epoch_idx, epoch in enumerate(unique_epochs):
    for batch_idx, batch in enumerate(unique_batches):
        image_name = f"ResultPics_{epoch}_batch{batch}.png"
        image_path = os.path.join(target_path, image_name)
        if os.path.exists(image_path):                        
            # 이미지의 각 영역을 추출
            cover_img, container_img, \
                clean_img, secret, \
                    rev_secret, rev_container_secret, img_metrics\
                        = process_data(image_path, col_index, netR)
            
            # 시각화 용으로 이미지 concat
            concat1 = np.concatenate((cover_img, container_img), axis=0)
            concat2 = np.concatenate((secret, rev_secret), axis=0)
            concat3 = np.concatenate((clean_img, rev_container_secret), axis=1)
            concat_image = np.concatenate((concat1, concat2), axis=1)
            concat_image = np.concatenate((concat_image, concat3), axis=0)
            concat_image = (concat_image - np.min(concat_image)) / (np.max(concat_image) - np.min(concat_image))
            
            image_metrics = [('I-PSNR', img_metrics[0]), ('I-SSIM', img_metrics[1]), 
                                # ('S-PSNR', img_metrics[2]), ('S-SSIM', img_metrics[3]),
                                ('R-PSNR', img_metrics[4]), ('R-SSIM', img_metrics[5])], ('F1-Score', img_metrics[6])

            visualize_image(fig, epoch_idx, batch_idx, unique_batches, concat_image, image_metrics)

            for metric_name, value in zip(metrics.keys(), img_metrics):
                metrics[metric_name].append(value)
                
    for metric_name, value in zip(metrics.keys(), metrics.values()):
        epoch_metrics[f"{metric_name}"].append(np.mean(value))
    
for metric_name, value in zip(metrics.keys(), metrics.values()):
    total_metrics[f"{metric_name}"].append(np.mean(value))

plt.tight_layout()
plt.subplots_adjust(hspace=0.35, wspace=0.1)
plt.show()

print(f"Mean I-PSNR: {np.mean(total_metrics['ipsnr']):.4f}")
# print(f"Mean I-SSIM: {np.mean(total_metrics['issim']):.4f}")
# print(f"Mean S-PSNR: {np.mean(total_metrics['spsnr']):.4f}")
# print(f"Mean S-SSIM: {np.mean(total_metrics['sssim']):.4f}")
print(f"Mean R-PSNR: {np.mean(total_metrics['rpsnr']):.4f}")
# print(f"Mean R-SSIM: {np.mean(total_metrics['rssim']):.4f}")



Mean S-PSNR: 23.5156
Mean S-SSIM: 0.9386
Mean R-PSNR: 23.7978
Mean R-SSIM: 0.9632


In [72]:
crop_types = ['random', 'center', 'corner', 'variable']

fig = plt.figure(figsize=(15, 3 * len(unique_epochs)))
# fig.suptitle(f"{target_path.split('/')[2]}", y=1.0)
for epoch_idx, epoch in enumerate(unique_epochs):
    for batch_idx, batch in enumerate(unique_batches):
        image_name = f"ResultPics_{epoch}_batch{batch}.png"
        image_path = os.path.join(target_path, image_name)
        if os.path.exists(image_path):                        
            crop_set = 3
            concat_list = []
            for col_index in range(4):
                cover_img, container_img, \
                    clean_img, secret, \
                        rev_secret, rev_container_secret, img_metrics\
                            = process_data(image_path, col_index, netR, crop_types[crop_set])
            
                secret = resize(crop(secret, crop_types[crop_set]), (256, 256))
                concat = np.concatenate((secret, rev_container_secret), axis=0)
                concat_list.append(concat)
            
            concat_image = np.concatenate((concat_list[0], concat_list[1]), axis=1)
            concat_image = np.concatenate((concat_image, concat_list[2]), axis=1)
            concat_image = np.concatenate((concat_image, concat_list[3]), axis=1)
            
            concat_image = (concat_image - np.min(concat_image)) / (np.max(concat_image) - np.min(concat_image))
            
            image_metrics = [('I-PSNR', img_metrics[0]), ('I-SSIM', img_metrics[1]), 
                                ('S-PSNR', img_metrics[2]), ('S-SSIM', img_metrics[3]),
                                ('R-PSNR', img_metrics[4]), ('R-SSIM', img_metrics[5])]
            
            ax = fig.add_subplot(len(unique_epochs), len(unique_batches), epoch_idx * len(unique_batches) + batch_idx + 1)
            ax.imshow(concat_image)
            ax.axis('off')
            ax.set_title(f"{epoch} : batch{batch}")


In [ ]:
import os
import torch
import numpy as np
from PIL import Image
from models.HidingRes import HidingRes
from torchvision import transforms
from skimage.transform import resize
from skimage.metrics import peak_signal_noise_ratio as psnr
from skimage.metrics import structural_similarity as ssim
from sklearn.metrics import accuracy_score

def calculate_BER(original, reconstructed):
    original_bits = original.flatten()
    reconstructed_bits = reconstructed.flatten()
    bit_error_rate = np.sum(np.abs(original_bits - reconstructed_bits)) / len(original_bits)
    return bit_error_rate

def calculate_SSIM(original, reconstructed):
    original = np.moveaxis(original, 0, -1)
    reconstructed = np.moveaxis(reconstructed, 0, -1)
    min_side = min(original.shape[0], original.shape[1])
    win_size = min_side if min_side % 2 == 1 else min_side - 1
    return ssim(original, reconstructed, win_size=win_size, data_range=1.0, multichannel=True, channel_axis=2)

def calculate_MSE(original, reconstructed):
    return np.mean((original - reconstructed) ** 2)

Rnet_path = './checkPointsoutputs/gold__2023-11-07-16_04_58/checkPoints/netR_epoch_38,sumloss=0.343609,Rloss=0.023546.pth'
os.path.exists(Rnet_path)

Rnet = HidingRes(in_c=1, out_c=1)
Rnet.cuda()

Rnet.load_state_dict(torch.load(Rnet_path))
Rnet = torch.nn.DataParallel(Rnet).cuda()
mse_loss = torch.nn.MSELoss().cuda()

resizer = transforms.Resize((256, 256))
loader = transforms.Compose([transforms.Resize((256, 256)), transforms.ToTensor()])

secret_img = imread("./60000.png")
secret_img = Image.fromarray(secret_img)
secret_img = resizer(secret_img)
secret_img = loader(secret_img)
secret_img_np = secret_img.cpu().numpy()

unique_batches = ["0100", "0300", "0700", '1000', '1200', '1500', '1700']
for idx,epoch in enumerate(unique_epochs):
    if idx > 5:
        break
    epoch_ber = []
    epoch_ssim = []
    epoch_acc = []
    bit_error_rate = []
    visual_quality = []
    extraction_acc = []
    fig, axs = plt.subplots(1, len(unique_batches), figsize=(15, 5), gridspec_kw={'wspace': 0.01, 'hspace': 0.01})
    fig.subplots_adjust(top=0.85)
    for i, batch in enumerate(unique_batches):        
        # print(epoch, batch)
        image_name = f"ResultPics_{epoch}_batch{batch}.png"
        image_path = os.path.join(folder_path, image_name)
        image = imread(image_path)

        cover_img = resize(image[258:513, 1:256], (256, 256))
        container_img = resize(image[258*4:256*5, 1:256], (256, 256))
        combined_image = np.concatenate((cover_img, container_img), axis=0)

        min_side = min(cover_img.shape[0], cover_img.shape[1])
        win_size = min_side if min_side % 2 == 1 else min_side - 1
        psnr_img= psnr(cover_img, container_img)
        ssim_img = ssim(cover_img, container_img, win_size=win_size, multichannel=True, channel_axis=2, data_range=1)                
        axs[i].text(13, 695+115, f"PSNR: {psnr_img:.4f}", fontsize=10, color='white', bbox=dict(facecolor='black', alpha=0.75))
        axs[i].text(13, 755+115, f"SSIM: {ssim_img:.4f}", fontsize=10, color='white', bbox=dict(facecolor='black', alpha=0.75))
        
        container_img = np.dot(container_img[...,:3], [0.2989, 0.5870, 0.1140])
        container_img_tensor = torch.from_numpy(container_img).float().unsqueeze(0).unsqueeze(0).cuda()       

        ext_wm = Rnet(container_img_tensor)
        ext_wm = ext_wm.detach().cpu().numpy().squeeze()
        ext_wm = np.clip(ext_wm, 0, 1)  
        ext_wm = np.expand_dims(ext_wm, axis=2)
        
        combined_image = np.dot(combined_image[...,:3], [0.2989, 0.5870, 0.1140])
        combined_image = np.expand_dims(combined_image, axis=-1)
        ext_wm_resized = np.resize(ext_wm, (ext_wm.shape[0], combined_image.shape[1], 1))
        combined_image = np.concatenate((combined_image, ext_wm), axis=0)
        
        ### Extracted watermark vs original watermark
        ext_wm = np.moveaxis(ext_wm, -1, 0)
        acc = calculate_MSE(ext_wm, secret_img_np)
        ext_ber = calculate_BER(ext_wm, secret_img_np) 
        ext_ssim = calculate_SSIM(ext_wm, secret_img_np)
        axs[i].text(13, 755+60+115, f"ext_BER: {ext_ber:.4f}", fontsize=10, color='white', bbox=dict(facecolor='black', alpha=0.75))
        axs[i].text(13, 755+120+115, f"ext_SSIM: {ext_ssim:.4f}", fontsize=10, color='white', bbox=dict(facecolor='black', alpha=0.75))
        
        axs[i].imshow(combined_image, cmap='gray')
        axs[i].set_title(f"Batch {batch}")
        axs[i].axis('off')
    
    fig.suptitle(f"Epoch {epoch}", y=0.95)
    plt.show()   
        


In [ ]:
import os
import torch
import numpy as np
from PIL import Image
from skimage.transform import resize
from models.HidingRes import HidingRes
from torchvision import transforms

Rnet_path = './checkPointsoutputs/gold__2023-11-07-16_04_58/checkPoints/netR_epoch_38,sumloss=0.343609,Rloss=0.023546.pth'
os.path.exists(Rnet_path)

Rnet = HidingRes(in_c=1, out_c=1)
Rnet.cuda()

Rnet.load_state_dict(torch.load(Rnet_path))
Rnet = torch.nn.DataParallel(Rnet).cuda()
mse_loss = torch.nn.MSELoss().cuda()

resizer = transforms.Resize((256, 256))
loader = transforms.Compose([transforms.Resize((256, 256)), transforms.ToTensor()])

secret_img = imread("./60000.png")
secret_img = Image.fromarray(secret_img)
secret_img = resizer(secret_img)
secret_img = loader(secret_img)

unique_batches = ["0100", "0300", "0700", '1000', '1200', '1500', '1700']
for idx,epoch in enumerate(unique_epochs):
    if idx > 5:
        break
    fig, axs = plt.subplots(1, len(unique_batches), figsize=(15, 5), gridspec_kw={'wspace': 0.01, 'hspace': 0.01})
    fig.subplots_adjust(top=0.85)
    for i, batch in enumerate(unique_batches):        
        image_name = f"ResultPics_{epoch}_batch{batch}.png"
        image_path = os.path.join(folder_path, image_name)
        image = imread(image_path)

        cover_img = image[258:513, 1:256]        
        cover_img = resize(cover_img, (256, 256))
        container_img = image[258*4:256*5, 1:256]
        container_img = resize(container_img, (256, 256))
        
        if container_img.shape[-1] == 3:
            container_img = np.dot(container_img[...,:3], [0.2989, 0.5870, 0.1140])

        container_img_tensor = torch.from_numpy(container_img).float().unsqueeze(0).unsqueeze(0).cuda()       
        
        ext_wm = Rnet(container_img_tensor)
        ext_wm = ext_wm.detach().cpu().numpy().squeeze()
        ext_wm = np.clip(ext_wm, 0, 1)  
        ext_wm = resize(ext_wm, (256, 256))
        ext_wm = np.expand_dims(ext_wm, axis=2)

        ext_wm_tensor = torch.from_numpy(ext_wm).float().unsqueeze(0).unsqueeze(0).cuda()
        secret_img_tensor = secret_img.unsqueeze(0).unsqueeze(0).cuda()

        errR_mse = 10000 * mse_loss(ext_wm_tensor, secret_img_tensor)
        # container_img = np.concatenate((container_img, ext_wm), axis=2)                
        # combined_image = np.concatenate((cover_img, container_img), axis=0) 

        axs[i].imshow(ext_wm, cmap='gray')
        axs[i].set_title(f"Batch {batch}")
        axs[i].axis('off')
        
    fig.suptitle(f"Epoch {epoch}", y=0.75)
    plt.show()

In [ ]:
import numpy as np
from skimage.metrics import peak_signal_noise_ratio, structural_similarity
from skimage.transform import resize

psnr_values = []
ssim_values = []


for epoch in unique_epochs:
    epoch_psnr_values = []
    epoch_ssim_values = []
    fig, axs = plt.subplots(1, len(unique_batches), figsize=(15, 5), gridspec_kw={'wspace': 0.01, 'hspace': 0.01})
    fig.subplots_adjust(top=0.85)
    for i, batch in enumerate(unique_batches):
        image_name = f"ResultPics_{epoch}_batch{batch}.png"
        image_path = os.path.join(folder_path, image_name)
        image = imread(image_path)

        image1 = image[258:513, 1:256]
        image2 = image[258*4:256*5, 1:256]
        
        resized_image1 = resize(image1, (256, 256))
        resized_image2 = resize(image2, (256, 256))

        combined_image = np.concatenate((resized_image1, resized_image2), axis=0) 

        axs[i].imshow(combined_image)
        axs[i].set_title(f"Batch {batch}")
        axs[i].axis('off')
        
        min_side = min(resized_image1.shape[0], resized_image1.shape[1])
        win_size = min_side if min_side % 2 == 1 else min_side - 1

        psnr = peak_signal_noise_ratio(resized_image1, resized_image2)
        ssim = structural_similarity(resized_image1, resized_image2, win_size=win_size, multichannel=True, channel_axis=2, data_range=1)                
        axs[i].text(0, 512, f"PSNR: {psnr:.4f}", fontsize=10, color='white', bbox=dict(facecolor='black', alpha=0.75))
        axs[i].text(0, 550, f"SSIM: {ssim:.4f}", fontsize=10, color='white', bbox=dict(facecolor='black', alpha=0.75))
        
        epoch_psnr_values.append(psnr)
        epoch_ssim_values.append(ssim)
        
    psnr_values.append(np.mean(epoch_psnr_values))
    ssim_values.append(np.mean(epoch_ssim_values))
        
    fig.suptitle(f"Epoch {epoch}", y=0.95)
    # plt.show()

plt.plot(unique_epochs, psnr_values)
plt.title("PSNR")
plt.plot(unique_epochs, ssim_values)
plt.title("SSIM")
